## Test importing gp_constr model in jupyter

In [1]:
# Import stuff
import sys, os

import plotly
import plotly.plotly as pltly
import plotly.graph_objs as go
import plotly.offline as pltlyoff
from IPython.display import display, HTML

import numpy as np
import scipy as sp
import itertools
import pyDOE

# Custom files
dir_PlottingFunctions = 'C:\\Data\\git repos\\gp-experiments\\'
dir_gp_constr = 'C:\\Data\\git repos\\'

sys.path.append(dir_PlottingFunctions) 
sys.path.append(dir_gp_constr) 

from PlottingFunctions import GPPlotly
from gp_constr.gp_model import kernel_RBF, GPmodel, Constraint

# Setup
pltlyoff.init_notebook_mode(connected=True)
print('Python version', sys.version)
#print('Plotly version', plotly.__version__)

Loading R wrapper...
Running R from rpy2: R version 3.4.3 (2017-11-30)


Python version 3.6.3 (v3.6.3:2c5fed8, Oct  3 2017, 18:11:49) [MSC v.1900 64 bit (AMD64)]


In [2]:
# Function to emulate
def fun(x):
    return (np.arctan(20*x - 10) - np.arctan(-10))/3

# Design data - no noise
x_design = np.array([1/(n+2) for n in range(7)] ) + 0.1
y_design = fun(x_design)

# Design data - noise
n = 50
noise_std = 0.2

#x_design = np.array(list(np.random.uniform(0.4, 0.7, n)) + list(np.random.uniform(0, 1, 10)))
#y_design = fun(x_design) + np.random.normal(0, noise_std, n+10)

#x_design = np.random.uniform(0.1, 0.8, n)
#y_design = fun(x_design) + np.random.normal(0, noise_std, n)

# For plotting
x_test = np.linspace(0, 1, 500)
y_true = fun(x_test)

### Create GP model ###

# Set up model
ker = kernel_RBF(variance = 0.5, lengthscale = [0.1])

model = GPmodel(kernel = ker, likelihood = 1E-6, mean = 0) # No Noise
#model = GPmodel(kernel = ker, likelihood = 1, mean = 0) # Noise

# Training data
model.X_training = x_design.reshape(-1, 1)
model.Y_training = y_design

# Add constraints
def constant_function(val):
    """ Return the constant function"""
    def fun(x):
        return np.array([val]*x.shape[0])
    
    return fun

# Boundedness
def fun_UB(x):
    return np.log(30*x.flatten() + 1)/3 + 0.1
    #return fun(x.flatten()) + 0.5
    
def fun_LB(x):
    f = np.log(30*x.flatten() + 1)/3 - 0.5
    f[x.flatten() < 0.6] = 0
    return f
    #return fun(x.flatten()) + 0.5

#constr_bounded = Constraint(LB = fun_LB, UB = fun_UB)
constr_bounded = Constraint(LB = constant_function(0), UB = fun_UB)

# Derivative
constr_deriv = Constraint(LB = constant_function(0), UB = constant_function(float('Inf')))

# Virtual points seed set 
Xv = np.linspace(0, 1, 20).reshape(-1, 1)
constr_bounded.Xv = Xv
constr_deriv.Xv = Xv

# Set constraints on model
model.constr_bounded = constr_bounded
model.constr_deriv = [constr_deriv]
model.constr_likelihood = 1E-6

# Optimize
#model.optimize(include_constraint = False, fix_likelihood = True)
print(model)

# Plot unconstrained un-optimized GP
mean_unconstr, cov_unconstr = model.calc_posterior_unconstrained(x_test.reshape(-1, 1), full_cov = True)
mean_unconstr = np.array(mean_unconstr).flatten()
var_unconstr = np.diagonal(cov_unconstr)

num_samples = 30
show_samplepaths = True
samplepaths_unconstr = []
if show_samplepaths: samplepaths_unconstr = np.random.multivariate_normal(mean_unconstr, cov_unconstr, num_samples).T

#x_true = x_test, y_true = y_true,
fig_unconstr_1 = GPPlotly.PlotGP2d(x_mean = x_test, mean = mean_unconstr, var = var_unconstr,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        num_std = 1.2815,
                        x_true = x_test, y_true = y_true,
                        title = '', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)

fig_unconstr_2 = GPPlotly.PlotGP2d(x_mean = x_test, mean = mean_unconstr, var = var_unconstr,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        samplepaths = samplepaths_unconstr, title = '', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)


trace_UB = go.Scatter(x = x_test, y = model.constr_bounded.UB(x_test), mode = 'lines', name = 'Upper bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
trace_LB = go.Scatter(x = x_test, y = model.constr_bounded.LB(x_test), mode = 'lines', name = 'Lower bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
                      
fig_unconstr_1 = GPPlotly.add_traces_to_fig(fig_unconstr_1, [trace_UB, trace_LB])

fig_unconstr_2 = GPPlotly.add_traces_to_fig(fig_unconstr_2, [trace_UB, trace_LB])
fig_unconstr_2 = go.Figure(data = fig_unconstr_2.data[3:], layout = fig_unconstr_2.layout)

print('\n Plotting unconstrained GP - Hyperparameters NOT optimized')
#fig_unconstr_1.layout['legend'] = dict(font = dict(size = 5), tracegroupgap = 0.001)
pltlyoff.iplot(fig_unconstr_1, filename='')
pltlyoff.iplot(fig_unconstr_2, filename='')

----- GP model ----- 
 mean = 0 
 likelihood = 1e-06 
 kernel: 
   type = RBF 
   input dim = 1 
   lenghtscale = [0.1] 
   variance = 0.5 
 constraint: 
   f [20], df/dx_1 [20] 
   constr_likelihood = 1e-06 
---------------------
..Running calculation of K_w ... DONE - time: 0.000 seconds
..Running calculation of Cholesky factor for K_w ... DONE - time: 0.000 seconds
..Calculating f* | Y ... DONE - Total time: 0.000 seconds

 Plotting unconstrained GP - Hyperparameters NOT optimized


Only boundedness

In [3]:
# Set up model

model.constr_deriv = None
model.constr_bounded.Xv = None

print(model)

----- GP model ----- 
 mean = 0 
 likelihood = 1e-06 
 kernel: 
   type = RBF 
   input dim = 1 
   lenghtscale = [0.1] 
   variance = 0.5 
 constraint: 
   f [0] 
   constr_likelihood = 1e-06 
---------------------


In [4]:
# Find XV for boundedness
bounds = [(0.001, 1)]
p_target = 0.90

df = model.find_XV_subop(bounds, p_target, i_range = [0])

XV_bound = model.constr_bounded.Xv

print(model)

Searching for points XV s.t. P(a - nu < Lf < b + nu) > p_target = 0.9 for Lf = [f] and nu = 1.2815515655446004e-06 ...
i = 0, XV[1] = [0.00100539], prob = 0.06711031353070473, acc. rate = 1, optimization time = 0.161 seconds
i = 0, XV[2] = [0.93976341], prob = 0.45963493469114475, acc. rate = 1, optimization time = 0.171 seconds
i = 0, XV[3] = [0.06874277], prob = 0.5490801502190613, acc. rate = 0.030846168715979116, optimization time = 0.449 seconds
i = 0, XV[4] = [0.78429117], prob = 0.5789208892220198, acc. rate = 0.016959502318571, optimization time = 0.307 seconds
i = 0, XV[5] = [0.99999952], prob = 0.7430289225908293, acc. rate = 0.009827590031647232, optimization time = 0.265 seconds
i = 0, XV[6] = [0.68485613], prob = 0.8179017307940801, acc. rate = 0.00733803834109029, optimization time = 0.122 seconds
i = 0, XV[7] = [0.85974519], prob = 0.8613336240545943, acc. rate = 0.006026229205758645, optimization time = 0.135 seconds
i = 0, XV[8] = [0.14946188], prob = 0.881228269620355

In [5]:
# Plot model

mean, var, perc, mode, samples = model.calc_posterior_constrained(x_test.reshape(-1, 1), compute_mode = False, num_samples = 10000, save_samples = 30, algorithm = 'minimax_tilting', resample = False)

mean = np.array(mean).flatten()
p_lower = perc[0]
median = perc[1]
p_upper = perc[2]
p_label = '[p{}, p{}]'.format(10, 90)

samplepaths_Z = []
if show_samplepaths: 
    samplepaths_Z = np.array(samples)

fig_bounded_1 = GPPlotly.PlotGP2d(x_mean = x_test, mean = mean,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        x_true = x_test, y_true = y_true,
                        p_lower = p_lower, p_upper = p_upper, p_label = p_label,
                        title = '', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)

fig_bounded_2 = GPPlotly.PlotGP2d(x_mean = x_test, mean = mean,
                        samplepaths =  samplepaths_Z,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        x_true = x_test, y_true = y_true,
                        p_lower = p_lower, p_upper = p_upper, p_label = p_label,
                        title = '', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)

trace_UB = go.Scatter(x = x_test, y = model.constr_bounded.UB(x_test), mode = 'lines', name = 'Upper bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
trace_LB = go.Scatter(x = x_test, y = model.constr_bounded.LB(x_test), mode = 'lines', name = 'Lower bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
trace_XV_bounded = go.Scatter(x = model.constr_bounded.Xv.flatten(), y = np.zeros(model.constr_bounded.Xv.shape[0]), mode = 'markers', name = 'Xv - boundedness', marker = dict(symbol = 'line-ns-open', color = ('rgb(0, 0, 0)')))

fig_bounded_1 = GPPlotly.add_traces_to_fig(fig_bounded_1, [trace_UB, trace_LB, trace_XV_bounded])

fig_bounded_2 = GPPlotly.add_traces_to_fig(fig_bounded_2, [trace_UB, trace_LB, trace_XV_bounded])
fig_bounded_2 = go.Figure(data = fig_bounded_2.data[3:], layout = fig_bounded_2.layout)

print('\n Plotting BOUNDED GP - Hyperparameters NOT optimized')
pltlyoff.iplot(fig_unconstr_1, filename='')

pltlyoff.iplot(fig_bounded_1, filename='')
pltlyoff.iplot(fig_bounded_2, filename='')

..Running calculation of K_w ... SKIP - (cached)
..Running calculation of Cholesky factor for K_w ... SKIP - (cached)
..Running preparation step 1 - dependence on (XS, X) ... DONE - time: 0.016 seconds
..Running preparation step 2 - dependence on (XV, X) ... SKIP - (cached)
..Running preparation step 3 - dependence on (XS, XV, X) ... DONE - time: 0.000 seconds
..sampling 10000 times from truncated constraint distribution C~|C, Y DONE - time: 0.129 seconds
..sampling 10000 times from constrained GP f*|C, Ychol jitter added.. 8.635225203364659e-10
 DONE - time: 0.457 seconds
..computing statistics from samples DONE - time: 0.214 seconds
 DONE - Total time: 0.815 seconds

 Plotting BOUNDED GP - Hyperparameters NOT optimized
